In [1]:
from Word2Vec_train import *
from Word2Vec_preprocess import *

In [2]:
# Create an object of class containing utilites
utility_funcs = trainingUtil()

In [3]:
# Read Files and then eliminate all hex ASCII chars and retain vocab_chars
passwords_list = utility_funcs.read_file_lines("/home/rm/BE_Project/Embedding/Data/ascii_rockyou_less_than_thirty_two.txt")

In [17]:
# Take a peek into password file data:
print(passwords_list[200:210])

['december', 'morgan', 'mariposa', 'maria', 'gabriela', 'iloveyou2', 'bailey', 'jeremy', 'pamela', 'kimberly']


In [5]:
# Saving the modified list of passwords
with open("/home/rm/BE_Project/Embedding/Data/ascii_rockyou_less_than_thirty_two_cleaned.txt", "w") as modified_file:
    for password in passwords_list:
        if (password == ""):
            continue
        modified_file.write(password+"\n")

In [6]:
# Sanity Check
with open("/home/rm/BE_Project/Embedding/Data/ascii_rockyou_less_than_thirty_two_cleaned.txt", "r") as f:
    for i in range(5):
        print(f.readline())

123456

12345

123456789

password

iloveyou



In [3]:
# Create a custom tokenizer instance
# VOCAB_SIZE = 68 because 26 chars + 10 digits + 32 specials chars
VOCAB_SIZE = 68
INPUT_FILE_PATH = "/home/rm/BE_Project/Embedding/Data/ascii_rockyou_less_than_thirty_two_cleaned.txt"
PROB_THRESHOLD = 1e-5 
TARGET_PROB_FILTER = False
embedding_tokenizer = tokenizeCharacters(VOCAB_SIZE, INPUT_FILE_PATH, PROB_THRESHOLD, TARGET_PROB_FILTER)

In [4]:
# Fit the tokenizer to the save password dataset
embedding_tokenizer.create_tokenizer()
embedding_tokenizer.fit_tokenizer()

[+]  Tokenizer has been created.
[+]  Reading the password file into memory...
[+]  Success! Password file has been completely read.
[+]  Fitting the passwords and creating the dictionary...
[+]  Success!


In [5]:
# Sanity Check
!wc -l /home/rm/BE_Project/Embedding/Data/ascii_rockyou_less_than_thirty_two_cleaned.txt

14339470 /home/rm/BE_Project/Embedding/Data/ascii_rockyou_less_than_thirty_two_cleaned.txt


In [6]:
# Sanity check -- see tokenizer configuration
embedding_tokenizer.tokenizer_config()

{'num_words': 68, 'filters': '', 'lower': True, 'split': ' ', 'char_level': True, 'oov_token': None, 'document_count': 14339470, 'word_counts': '{"1": 6729047, "2": 5234118, "3": 3765001, "4": 3389302, "5": 3352100, "6": 3115891, "7": 3098532, "8": 3565087, "9": 3852974, "p": 1751029, "a": 9432074, "s": 4468899, "w": 859106, "o": 5502471, "r": 4896159, "d": 2683172, "i": 5909287, "l": 4791665, "v": 1126897, "e": 7662524, "y": 2534225, "u": 2444243, "n": 5144186, "c": 2817141, "k": 2156089, "b": 2298741, "g": 1847132, "m": 3464853, "j": 1359656, "h": 2497711, "q": 196395, "t": 3674077, "0": 5734965, "f": 1062344, "z": 816904, "x": 515213, "!": 142869, ";": 12252, "-": 132978, "*": 123832, ".": 248465, "?": 18274, ",": 29740, "/": 48166, "#": 48839, "@": 107737, "$": 36024, "%": 10251, "^": 6391, "&": 26357, "+": 26985, "\'": 15321, "[": 7682, "]": 10792, "<": 9558, "_": 192872, ">": 2456, "=": 18362, "\\\\": 25730, "\\"": 3637, ":": 6847, "(": 17034, ")": 18959, "`": 5447, "~": 8327, "{

In [7]:
# Saving the tokenizer Configuration for later use in model
embedding_tokenizer.save_tokenizer_config("/home/rm/BE_Project/Embedding/Tokenizer_Config/tokenizer_rockyou")

In [8]:
# Sanity Check -- Test Embedding 
test_pass = ["mypass", "pass"]
embedding_tokenizer.tokenizer.texts_to_sequences(test_pass)

[[16, 23, 29, 1, 11, 11], [29, 1, 11, 11]]

In [9]:
# Create Custom Skipgrams instance and pass the output of tokenizer
SKIP_WINDOW_SIZE = 2
NUM_NEG_SAMPLES = 4.0
ENABLE_SAMPLING_TABLE_USING_FREQUENCY = True
SKIP_SHUFFLE = True
SKIP_CATEGORICAL = False
emb_skip = createSkipGrams(VOCAB_SIZE, SKIP_WINDOW_SIZE, NUM_NEG_SAMPLES, SKIP_SHUFFLE, SKIP_CATEGORICAL, ENABLE_SAMPLING_TABLE_USING_FREQUENCY)
emb_skip.preprocessing_rank_word(embedding_tokenizer.tokenizer, type = "zipf")
print(emb_skip.sampling_table.shape)

[+]  Success! Sampling table has been created!
(69,)


In [10]:
def encode_and_save():
    BUFFER_SIZE = 500
    total_count = 0
    clean_pass_file = open("/home/rm/BE_Project/Embedding/Data/ascii_rockyou_less_than_thirty_two_cleaned.txt", "r")
    buffer_pass_list = []
    while True:
        for i in range(BUFFER_SIZE):
            single_pass = clean_pass_file.readline()
            if(single_pass == ""):
                print("The total number of passwords read from memory were: ", total_count)
                clean_pass_file.close()
                return
            else:
                buffer_pass_list.append(single_pass)
            if(i == (BUFFER_SIZE - 1)):
                print(f"Processing buffer batch {math.ceil(total_count / BUFFER_SIZE)}")
                buffer_pass_list = embedding_tokenizer.tokenizer.texts_to_sequences(buffer_pass_list)
                total_count += BUFFER_SIZE
                x,y = emb_skip.create_skipgrams(buffer_pass_list, embedding_tokenizer.tokenizer) 
                utility_funcs.save_data(x, y, "/home/rm/BE_Project/Embedding/Data/encoded_passwords")
                buffer_pass_list = [] # Empty the list again


In [11]:
# Storing the encoded data to the disk -- helping to split later and feed into model -- Will take a lot of time
encode_and_save()

Processing buffer batch 0
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 1
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 2
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 3
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 4
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 5
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 6
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 7
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 

[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 68
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 69
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 70
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 71
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 72
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 73
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 74
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 75
[+]  Skipgrams h

[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 143
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 144
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 145
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 146
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 147
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 148
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 149
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 150
[+]  Ski

[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 216
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 217
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 218
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 219
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 220
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 221
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 222
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 223
[+]  Ski

[+]  Success! New set appended.
Processing buffer batch 292
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 293
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 294
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 295
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 296
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 297
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 298
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 299
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Suc

...

[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28380
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28381
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28382
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28383
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28384
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28385
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28386
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batc

[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28453
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28454
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28455
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28456
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28457
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28458
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28459
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batc

[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28531
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28532
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28533
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28534
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28535
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28536
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28537
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batc

[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28602
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28603
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28604
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28605
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28606
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28607
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28608
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batc

[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28669
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28670
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28671
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28672
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28673
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28674
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batch 28675
[+]  Skipgrams have been created.
[+]  Appending to the file...
[+]  Success! New set appended.
Processing buffer batc

In [10]:
# Check the number of examples in the csv file
!wc -l /home/rm/BE_Project/Embedding/Data/encoded_passwords.csv

38172735 /home/rm/BE_Project/Embedding/Data/encoded_passwords.csv


In [11]:
# Check the sizes of both train and validation sets
!wc -l /home/rm/BE_Project/Embedding/Data/train/train_encoded_passwords.csv
!wc -l /home/rm/BE_Project/Embedding/Data/validation/valid_encoded_passwords.csv

34355461 /home/rm/BE_Project/Embedding/Data/train/train_encoded_passwords.csv
3817274 /home/rm/BE_Project/Embedding/Data/validation/valid_encoded_passwords.csv


In [12]:
# Creating the model instance for training
# Defining the hyperparameters:
import time
OPTIMIZER = "adam"
LEARNING_RATE = 0.01
METRICS = [tf.keras.metrics.BinaryAccuracy()]
MODEL_SAVE_FORMAT = "default"
WT_SAVE_FORMAT = "tf"
EMBEDDING_DIM = 16
ENABLE_MODEL_CHECKPOINT = True
BATCH_SIZE = 32
VALIDATION_BATCH_SIZE = 32 
EPOCHS = 5
VALIDATION_FREQ = 1
TRAIN_SEQ_WORKERS = 4
USE_MULTIPROCESSING = True
EMBED_REGULARIZER = False
VISUALIZE_DIR = "/home/rm/BE_Project/Embedding/Tensorboard_Log"
TENSORBOARD_NAME = f"char_embedding_model-{int(time.time())}"
TENSORBOARD_LOG_DIR = "/home/rm/BE_Project/Embedding/Tensorboard_Visualize/"+TENSORBOARD_NAME

In [13]:
# Split the csv into two sets for training and validation for tuning hyperparameters
FILE_PATH = "/home/rm/BE_Project/Embedding/Data/encoded_passwords.csv"
TRAIN_PATH = "/home/rm/BE_Project/Embedding/Data/train/train_encoded_passwords"
TEST_PATH = "/home/rm/BE_Project/Embedding/Data/validation/valid_encoded_passwords"
TEST_SPLIT_SIZE = 0.10
utility_funcs.split_data(FILE_PATH, TRAIN_PATH, TEST_PATH, TEST_SPLIT_SIZE)

[+]  Appending to the file...
[+]  Success! New set appended.
[+]  Appending to the file...
[+]  Success! New set appended.


In [13]:
emb_model = modelOperations(ENABLE_MODEL_CHECKPOINT, EMBED_REGULARIZER, embedding_tokenizer.tokenizer, VOCAB_SIZE, EMBEDDING_DIM, VISUALIZE_DIR, TENSORBOARD_LOG_DIR)   

In [14]:
# Initialize the model with weights and stuff
emb_model.create_embedding_model()
CHECKPOINT_PATH = "/home/rm/BE_Project/Embedding/Model_Checkpoints"
emb_model.model_checkpoint_callback(CHECKPOINT_PATH)
emb_model.setup_model_tensorboard()
emb_model.optimizer_instance(OPTIMIZER)
emb_model.model_compile(METRICS)
emb_model.print_model_summary()

Remember the models needs to be compiled later on.
[+]  Writing metadata to the tensorboard logging dir.
[+]  Directory path doesn't exist, making a new directory for saving metadata.
[+]  Success!
[+]  Creating a custom callback to write the embeddings at the end of each epoch..
[+]  Model has been successfully compiled.
Model: "model"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            [(None, 1)]          0                                            
__________________________________________________________________________________________________
input_2 (InputLayer)            [(None, 1)]          0                                            
__________________________________________________________________________________________________
target_embedding (Embedding)    (None, 1, 16)        1104        in

In [15]:
# Start fitting the model -- Training will take a long time
# Define the parameters for fitting
TRAIN_FILE_PATH = "/home/rm/BE_Project/Embedding/Data/train/train_encoded_passwords.csv"
VALIDATION_FILE_PATH = "/home/rm/BE_Project/Embedding/Data/validation/valid_encoded_passwords.csv"
VERBOSE = 1
SHUFFLE = 'batch'
emb_model.model_fit(TRAIN_FILE_PATH, VALIDATION_FILE_PATH, BATCH_SIZE, VALIDATION_BATCH_SIZE, EPOCHS, VERBOSE, SHUFFLE, TRAIN_SEQ_WORKERS, USE_MULTIPROCESSING, VALIDATION_FREQ)

[+]  WARNING: some of the validation data may not be used. (size < Validation Batch Size). To reduce the unused data, lower the validation batch size.
[+]  Fitting the model...
Epoch 1/5
1073607/1073608 [============================>.] - ETA: 0s - loss: 0.3297 - binary_accuracy: 0.8347WARNING:tensorflow:multiprocessing can interact badly with TensorFlow, causing nondeterministic deadlocks. For high performance data pipelines tf.data is recommended.

Epoch 00001: saving model to /home/rm/BE_Project/Embedding/Model_Checkpoints_001
Instructions for updating:
If using Keras pass *_constraint arguments to layers.
INFO:tensorflow:Assets written to: /home/rm/BE_Project/Embedding/Model_Checkpoints_001/assets
1073608/1073608 [==============================] - 117838s 110ms/step - loss: 0.3297 - binary_accuracy: 0.8347 - val_loss: 0.3316 - val_binary_accuracy: 0.8350
Epoch 2/5


1073608/1073608 [==============================] - ETA: 0s - loss: 0.3296 - binary_accuracy: 0.8350WARNING:tensorflow:multiprocessing can interact badly with TensorFlow, causing nondeterministic deadlocks. For high performance data pipelines tf.data is recommended.

Epoch 00002: saving model to /home/rm/BE_Project/Embedding/Model_Checkpoints_002
INFO:tensorflow:Assets written to: /home/rm/BE_Project/Embedding/Model_Checkpoints_002/assets
1073608/1073608 [==============================] - 165000s 154ms/step - loss: 0.3296 - binary_accuracy: 0.8350 - val_loss: 0.3291 - val_binary_accuracy: 0.8351
Epoch 3/5
1073607/1073608 [============================>.] - ETA: 0s - loss: 0.3299 - binary_accuracy: 0.8350WARNING:tensorflow:multiprocessing can interact badly with TensorFlow, causing nondeterministic deadlocks. For high performance data pipelines tf.data is recommended.

Epoch 00003: saving model to /home/rm/BE_Project/Embedding/Model_Checkpoints_003
INFO:tensorflow:Assets written to: /home